In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 5.5 MB 28.0 MB/s 
     |████████████████████████████████| 182 kB 74.6 MB/s 
     |████████████████████████████████| 7.6 MB 61.1 MB/s 


In [ ]:
from transformers import AutoTokenizer, AutoModel
import random, math
from typing import Union
import numpy as np
import torch
from torch import Tensor
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import DataLoader
from tqdm.auto import tqdm
import transformers
from sklearn.model_selection import cross_validate
from sklearn.model_selection import KFold 
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score

def load_datasets() -> Union[dict, dict]:

    import json
    import os
    
    train = {}
    test = {}

    train_df = pd.read_csv(r'/content/drive/MyDrive/dreaddit/dreaddit-train.csv')
    test_df = pd.read_csv(r'/content/drive/MyDrive/dreaddit/dreaddit-test.csv')
        
    train["texts"] = train_df.text.tolist() 
    train["label"] = train_df.label.tolist() 

    test["texts"] = test_df.text.tolist()
    test["label"] = test_df.label.tolist()
    
    return train, test

class Dataset(torch.utils.data.Dataset):
    def __init__(self, data_dict: dict):
        self.data_dict = data_dict
        dd = data_dict

    def __len__(self):
        return len(self.data_dict["texts"])

    def __getitem__(self, idx):
        dd = self.data_dict
        return dd["texts"][idx], dd["label"][idx]


def train_BiLSTM(model, loader, device):
    model.train()
    criterion = model.get_criterion()
    total_loss = 0.0
    
    for X,y in tqdm(loader):
        
        optimizer.zero_grad()

        inputs = model.embedding(X).to(device)
        target = y.to(device, dtype=torch.float32)
        
        pred = model(inputs).squeeze()
        pred = torch.sigmoid(pred)

        loss = criterion(pred, target)
        # loss = F.binary_cross_entropy(pred, target)
        
        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    return total_loss / len(loader)

@torch.no_grad()
def eval_mentalbert(model, loader, device):
    model.eval()

    targets = []
    preds = []
    for X,y in tqdm(loader):
        #print(len(X))
        optimizer.zero_grad()

        inputs = model.embedding(X).to(device)
        target = y.to(device, dtype=torch.float32)

        pred = model(inputs).squeeze()
        pred = torch.sigmoid(pred)

        preds.append(pred)
        targets.append(target)
    #print(preds)

    return torch.cat(preds), torch.cat(targets)

class BiLSTM(nn.Module):

    def __init__(self):
        super(BiLSTM, self).__init__()
        
        self.tokenizer = AutoTokenizer.from_pretrained("mental/mental-bert-base-uncased")
        self.pretrained_model = AutoModel.from_pretrained("mental/mental-bert-base-uncased")

        self.hidden_size = 64
        drp = 0.1
        # self.embedding = nn.Embedding(max_features, embed_size)
        # self.embedding.weight = nn.Parameter(torch.tensor(embedding_matrix, dtype=torch.float32))
        # self.embedding.weight.requires_grad = False
        self.lstm = nn.LSTM(768, self.hidden_size, bidirectional=True, batch_first=True)
        self.linear = nn.Linear(self.hidden_size*4 , 64)
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(drp)
        self.out = nn.Linear(64, 1)
   
        self.criterion = torch.nn.BCEWithLogitsLoss(reduction='sum')
        
    def get_pretrained_model(self):
        return self.pretrained_model

    def get_tokenizer(self):
        return self.tokenizer
    
    def get_criterion(self):
        return self.criterion

    def assign_optimizer(self, lr=0.001):
        optimizer = torch.optim.Adam(filter(lambda p: p.requires_grad, model.parameters()), 
                                 lr=0.001)
        return optimizer

    def tokenize(
                self,
                texts: "list[str]",
                max_length: int = 100,
                truncation: bool = True,
                padding: bool = True,
            ):
                
                tokenizer = self.get_tokenizer()
                # print('------->>>',list(texts))

                tokenized = tokenizer(list(texts), 
                                        max_length = max_length, 
                                        truncation = True, 
                                        padding = True,
                                        return_tensors ="pt")
        
                return tokenized        


    def embedding(self, inputs):
        Model = self.get_pretrained_model()
        encoded_input = self.tokenize(inputs)
        # for t in encoded_input:
        # print('------->>>',encoded_input['input_ids'].shape)
        Model.eval()
        # sentence_embeddings = []
        with torch.no_grad():
                model_output_train = Model(**encoded_input.to(device))
                hid_states = model_output_train[0]
                # print('------->>>',hid_states.shape)
                # tok_vecs = hid_states[-2]
                # print(tok_vecs.shape)
                # sentence_embeddings.extend(torch.mean(tok_vecs,dim=1))
        # print(len(sentence_embeddings))
        return hid_states.to(device)
    
    # Progresses data across layers    
   

    def forward(self, x):
        # h_embedding = self.embedding(x)
        # h_embedding = torch.squeeze(torch.unsqueeze(h_embedding, 0))
        
        h_lstm, _ = self.lstm(x)
        avg_pool = torch.mean(h_lstm, 1)
        max_pool, _ = torch.max(h_lstm, 1)
        #print("avg_pool", avg_pool.size())
        #print("max_pool", max_pool.size())
        conc = torch.cat(( avg_pool, max_pool), 1)
        conc = self.relu(self.linear(conc))
        conc = self.dropout(conc)
        out = self.out(conc)
        return out
    
    
if __name__ == "__main__":
    import pandas as pd

    random.seed(2022)
    torch.manual_seed(2022)

    sample_size = None  
    batch_size = 128
    n_epochs = 10
    num_words = 50000

    # If you use GPUs, use the code below:
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

    train_raw, test_raw = load_datasets()
    

    if sample_size is not None:
        for key in ["texts", "label"]:
            train_raw[key] = train_raw[key][:sample_size]
            test_raw[key] = test_raw[key][:sample_size]
    
    # print(len(train_raw['texts']))
    
    print("=" * 80)
    print("Running test code for part 1")
    print("-" * 80)


    test_loader = torch.utils.data.DataLoader(
        Dataset(test_raw), batch_size=batch_size, shuffle=False
    )


    X = np.array(train_raw['texts'])
    y = np.array(train_raw['label'])

    k = 10
    kf = KFold(n_splits=k, random_state=None)
    
    acc_train = []
    pr_train = []
    re_train = []
    f1_train = []

    acc_valid = []
    pr_valid = []
    re_valid = []
    f1_valid = []
    
    acc_test = []
    pr_test = []
    re_test = []
    f1_test = []    
    
     
    f = 0
    for train_index , test_index in kf.split(X):
        
        f+=1
        print('Fold', f, '>>>'*10) 
        
        train = {}
        valid = {}
        
        X_train , X_test = X[train_index], X[test_index]
        y_train , y_test = y[train_index] , y[test_index]
        
        train['texts'] = X_train.tolist()
        train['label'] = y_train.tolist()
        
        valid['texts'] = X_test.tolist()
        valid['label'] = y_test.tolist()

        train_loader = torch.utils.data.DataLoader(
            Dataset(train), batch_size=batch_size, shuffle=True
        )

        valid_loader = torch.utils.data.DataLoader(
            Dataset(valid), batch_size=batch_size, shuffle=False
        )
        
        # print('llllllll',len(valid['label']))
        
        model = BiLSTM().to(device)
        optimizer = model.assign_optimizer(lr=1e-4)
        
        train_accuracies = []
        train_precisions = []
        train_recalls = []
        train_f1_scores = []

        
        valid_accuracies = []
        valid_precisions = []
        valid_recalls = []
        valid_f1_scores = []        
        
        valid_accuracies = []
        
        previous_valid_accuracy = -1
        
        for epoch in range(n_epochs):

            loss = train_BiLSTM (model, train_loader, device=device)
    
            train_preds, train_targets = eval_mentalbert(model, train_loader, device=device)
            train_preds = train_preds.round()

            train_accuracy = accuracy_score(train_targets.cpu(), train_preds.cpu())
            train_accuracies.append(train_accuracy)
            train_precision = precision_score(train_targets.cpu(), train_preds.cpu())
            train_precisions.append(train_precision)
            train_recall = recall_score(train_targets.cpu(), train_preds.cpu())
            train_recalls.append(train_recall)
            train_f1 = f1_score(train_targets.cpu(), train_preds.cpu())
            train_f1_scores.append(train_f1)          
            

            eval_preds, eval_targets = eval_mentalbert(model, valid_loader, device=device)
            eval_preds = eval_preds.round()

            eval_accuracy = accuracy_score(eval_targets.cpu(), eval_preds.cpu())
            valid_accuracies.append(eval_accuracy)
            valid_precision = precision_score(eval_targets.cpu(), eval_preds.cpu())
            valid_precisions.append(valid_precision)
            valid_recall = recall_score(eval_targets.cpu(), eval_preds.cpu())
            valid_recalls.append(valid_recall)
            valid_f1_score = f1_score(eval_targets.cpu(), eval_preds.cpu())
            valid_f1_scores.append(valid_f1_score)
           
            print("Epoch:", epoch)
            print("Training loss:", loss)
            print("Train Accuracy:", train_accuracy)
            print("Validation Accuracy:", eval_accuracy)
    
            print('---'*10)   
            
            #if eval_accuracy < previous_valid_accuracy:
             #   break
            #else:
             #   previous_valid_accuracy = eval_accuracy
        
     
        acc_train.append(sum(train_accuracies)/len(train_accuracies))
        pr_train.append(sum(train_precisions)/len(train_precisions))
        re_train.append(sum(train_recalls)/len(train_recalls))
        f1_train.append(sum(train_f1_scores)/len(train_f1_scores))

        acc_valid.append(sum(valid_accuracies)/len(valid_accuracies))
        pr_valid.append(sum(valid_precisions)/len(valid_precisions))
        re_valid.append(sum(valid_recalls)/len(valid_recalls))
        f1_valid.append(sum(valid_f1_scores)/len(valid_f1_scores))
        
        print('---'*10) 


        test_preds, test_targets = eval_mentalbert(model, test_loader, device=device)
        test_preds = test_preds.round()
    
        test_accuracy = accuracy_score(test_targets.cpu(), test_preds.cpu())
        test_precision = precision_score(test_targets.cpu(), test_preds.cpu())
        test_recall = recall_score(test_targets.cpu(), test_preds.cpu())
        test_f1_score = f1_score(test_targets.cpu(), test_preds.cpu())
       
        print("TEST Accuracy:", test_accuracy)
        print("TEST Precision:", test_precision)
        print("TEST Recall:", test_recall)
        print("TEST F1_Score:", test_f1_score)
        
        
        acc_test.append(test_accuracy)
        pr_test.append(test_precision)
        re_test.append(test_recall)
        f1_test.append(test_f1_score)

        print('...'*10)
        
    print("Total Training Accuracy:", sum(acc_train)/len(acc_train))
    print("Total Training Preciion:", sum(pr_train)/len(pr_train))
    print("Total Training Recall:", sum(re_train)/len(re_train))
    print("Total Training F1_Score:", sum(f1_train)/len(f1_train))
    
    print('>>><<<'*10)

    print("Total Validation Accuracy:", sum(acc_valid)/len(acc_valid))
    print("Total Validation Precision:", sum(pr_valid)/len(pr_valid))
    print("Total Validation Recall:", sum(re_valid)/len(re_valid))
    print("Total Validation F1_Score:", sum(f1_valid)/len(f1_valid))

    print('>>><<<'*10)
    
    print("Total Test Accuracy:", sum(acc_test)/len(acc_test))
    print("Total Test Precision:", sum(pr_test)/len(pr_test))
    print("Total Test Recall:", sum(re_test)/len(re_test))
    print("Total Test F1_Score:", sum(f1_test)/len(f1_test))

    print('>>><<<'*10)



Running test code for part 1
--------------------------------------------------------------------------------
Fold 1 >>>>>>>>>>>>>>>>>>>>>>>>>>>>>>


Downloading:   0%|          | 0.00/321 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/232k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/466k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

...

  0%|          | 0/20 [00:00<?, ?it/s]

  0%|          | 0/3 [00:00<?, ?it/s]

Epoch: 9
Training loss: 70.11643142700196
Train Accuracy: 0.898238747553816
Validation Accuracy: 0.8056537102473498
------------------------------
------------------------------


  0%|          | 0/6 [00:00<?, ?it/s]

TEST Accuracy: 0.772027972027972
TEST Precision: 0.7942857142857143
TEST Recall: 0.7533875338753387
TEST F1_Score: 0.7732962447844228
..............................
Total Training Accuracy: 0.8089625314345174
Total Training Preciion: 0.8633048662864502
Total Training Recall: 0.7216656590995703
Total Training F1_Score: 0.7692203751798729
>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<
Total Validation Accuracy: 0.7612055193350918
Total Validation Precision: 0.8067677254914607
Total Validation Recall: 0.672692175080021
Total Validation F1_Score: 0.7198079129015065
>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<
Total Test Accuracy: 0.7783216783216782
Total Test Precision: 0.8131039897911225
Total Test Recall: 0.7425474254742548
Total Test F1_Score: 0.775321212241132
>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<>>><<<
